## Voice Style Control Demo

In [17]:
%%time
import os
import torch
from openvoice import se_extractor
from openvoice.api import BaseSpeakerTTS, ToneColorConverter

CPU times: user 15 µs, sys: 1e+03 ns, total: 16 µs
Wall time: 18.8 µs


### Initialization

In [18]:
ckpt_base = 'checkpoints/base_speakers/EN'
ckpt_converter = 'checkpoints/converter'
device="cuda:0" if torch.cuda.is_available() else "cpu"
output_dir = 'outputs'

base_speaker_tts = BaseSpeakerTTS(f'{ckpt_base}/config.json', device=device)
base_speaker_tts.load_ckpt(f'{ckpt_base}/checkpoint.pth')

tone_color_converter = ToneColorConverter(f'{ckpt_converter}/config.json', device=device)
tone_color_converter.load_ckpt(f'{ckpt_converter}/checkpoint.pth')

os.makedirs(output_dir, exist_ok=True)

Loaded checkpoint 'checkpoints/base_speakers/EN/checkpoint.pth'
missing/unexpected keys: [] []
Loaded checkpoint 'checkpoints/converter/checkpoint.pth'
missing/unexpected keys: [] []


### Obtain Tone Color Embedding

The `source_se` is the tone color embedding of the base speaker. 
It is an average of multiple sentences generated by the base speaker. We directly provide the result here but
the readers feel free to extract `source_se` by themselves.

In [19]:
source_se = torch.load(f'{ckpt_base}/en_default_se.pth').to(device)

The `reference_speaker.mp3` below points to the short audio clip of the reference whose voice we want to clone. We provide an example here. If you use your own reference speakers, please **make sure each speaker has a unique filename.** The `se_extractor` will save the `targeted_se` using the filename of the audio and **will not automatically overwrite.**

In [20]:
reference_speaker = './resources/demo_speaker0.mp3' # This is the voice you want to clone
target_se, audio_name = se_extractor.get_se(reference_speaker, tone_color_converter, target_dir='processed', vad=True)

OpenVoice version: v1
[(0.0, 19.278375)]
after vad: dur = 19.27798185941043


### Inference

In [21]:
save_path = f'{output_dir}/output_en_default.wav'

# Run the base speaker tts
text = "This audio is generated by OpenVoice."
src_path = f'{output_dir}/tmp.wav'
base_speaker_tts.tts(text, src_path, speaker='default', language='English', speed=1.0)

# Run the tone color converter
encode_message = "@MyShell"
tone_color_converter.convert(
    audio_src_path=src_path, 
    src_se=source_se, 
    tgt_se=target_se, 
    output_path=save_path,
    message=encode_message)

 > Text splitted to sentences.
This audio is generated by OpenVoice.
 > ===========================
ðɪs ˈɑdiˌoʊ ɪz ˈdʒɛnəɹˌeɪtɪd baɪ ˈoʊpən vɔɪs.
 length:45
 length:45


**Try with different styles and speed.** The style can be controlled by the `speaker` parameter in the `base_speaker_tts.tts` method. Available choices: friendly, cheerful, excited, sad, angry, terrified, shouting, whispering. Note that the tone color embedding need to be updated. The speed can be controlled by the `speed` parameter. Let's try whispering with speed 0.9.

In [22]:
source_se = torch.load(f'{ckpt_base}/en_style_se.pth').to(device)
save_path = f'{output_dir}/output_whispering.wav'

# Run the base speaker tts
text = "This audio is generated by OpenVoice."
src_path = f'{output_dir}/tmp.wav'
base_speaker_tts.tts(text, src_path, speaker='whispering', language='English', speed=0.9)

# Run the tone color converter
encode_message = "@MyShell"
tone_color_converter.convert(
    audio_src_path=src_path, 
    src_se=source_se, 
    tgt_se=target_se, 
    output_path=save_path,
    message=encode_message)

 > Text splitted to sentences.
This audio is generated by OpenVoice.
 > ===========================
ðɪs ˈɑdiˌoʊ ɪz ˈdʒɛnəɹˌeɪtɪd baɪ ˈoʊpən vɔɪs.
 length:45
 length:45


**Try with different languages.** OpenVoice can achieve multi-lingual voice cloning by simply replace the base speaker. We provide an example with a Chinese base speaker here and we encourage the readers to try `demo_part2.ipynb` for a detailed demo.

In [23]:
ckpt_base = 'checkpoints/base_speakers/ZH'
base_speaker_tts = BaseSpeakerTTS(f'{ckpt_base}/config.json', device=device)
base_speaker_tts.load_ckpt(f'{ckpt_base}/checkpoint.pth')

source_se = torch.load(f'{ckpt_base}/zh_default_se.pth').to(device)
save_path = f'{output_dir}/output_chinese.wav'


/Users/russell/miniconda3/envs/openvoice/lib/python3.9/site-packages/torch/nn/utils/weight_norm.py:28: UserWarning: torch.nn.utils.weight_norm is deprecated in favor of torch.nn.utils.parametrizations.weight_norm.
  warnings.warn("torch.nn.utils.weight_norm is deprecated in favor of torch.nn.utils.parametrizations.weight_norm.")


Loaded checkpoint 'checkpoints/base_speakers/ZH/checkpoint.pth'
missing/unexpected keys: [] []


In [24]:
%%time
# Run the base speaker tts
text = "毛岛灰绣眼鸟（学名：Zosterops mauritianus）是一种绣眼鸟科绣眼鸟属的鸟类，属于毛里求斯岛上两种特有种绣眼鸟之一，另一种是更为稀少的毛里求斯绣眼鸟。上半身整体为灰色，下半身为灰白色，臀部和腋羽是十分显眼的白色。这种鸟栖息于次生林、森林和花园中[1]。它与留尼汪灰绣眼鸟亲缘关系很近，曾经被认为是同种，统称为马斯克林绣眼鸟[2]"
src_path = f'{output_dir}/tmp.wav'
base_speaker_tts.tts(text, src_path, speaker='default', language='Chinese', speed=1.0)

# Run the tone color converter
encode_message = "@MyShell"
tone_color_converter.convert(
    audio_src_path=src_path, 
    src_se=source_se, 
    tgt_se=target_se, 
    output_path=save_path,
    message=encode_message)

 > Text splitted to sentences.
毛岛灰绣眼鸟（学名：Zosterops mauritianus）是一种绣眼鸟科绣眼鸟属的鸟类,
属于毛里求斯岛上两种特有种绣眼鸟之一,
另一种是更为稀少的毛里求斯绣眼鸟.
上半身整体为灰色, 下半身为灰白色,
臀部和腋羽是十分显眼的白色.
这种鸟栖息于次生林、森林和花园中[1].
它与留尼汪灰绣眼鸟亲缘关系很近,
曾经被认为是同种, 统称为马斯克林绣眼鸟[2]
 > ===========================
mɑʊ↑t⁼ɑʊ↓↑ xweɪ→ ʃjoʊ↓ jɛn↓↑niɑʊ↓↑（ ʃɥɛ↑miŋ↑,ts⁼eɪ↓oʊ→ɛ↑sɹ↓tʰi↓i↓a↓oʊ→pʰi→ɛ↑sɹ↓ ɛ↑mu↓eɪ→joʊ→a↓aɪ↓tʰi↓aɪ↓eɪ→ən→joʊ→ɛ↑sɹ↓） s`ɹ`↓ i→ts`⁼ʊŋ↓↑ ʃjoʊ↓ jɛn↓↑niɑʊ↓↑kʰə→ ʃjoʊ↓ jɛn↓↑niɑʊ↓↑ s`u↓↑ t⁼ə niɑʊ↓↑leɪ↓,
 length:199
 length:197
s`u↓↑ɥ↑ mɑʊ↑li↓↑tʃʰjoʊ↑sɹ→ t⁼ɑʊ↓↑s`ɑŋ↓ liɑŋ↓↑ts`⁼ʊŋ↓↑ tʰə↓joʊ↓↑ts`⁼ʊŋ↓↑ ʃjoʊ↓ jɛn↓↑niɑʊ↓↑ ts`⁼ɹ`→i→,
 length:100
 length:100
liŋ↓ i→ts`⁼ʊŋ↓↑ s`ɹ`↓ k⁼əŋ↓weɪ↑ ʃi→s`ɑʊ↓↑ t⁼ə mɑʊ↑li↓↑tʃʰjoʊ↑sɹ→ ʃjoʊ↓ jɛn↓↑niɑʊ↓↑.
 length:83
 length:83
s`ɑŋ↓p⁼an↓s`ən→ ts`⁼əŋ↓↑tʰi↓↑ weɪ↓ xweɪ→sə↓,  ʃja↓p⁼an↓s`ən→ weɪ↓ xweɪ→p⁼aɪ↑sə↓,
 length:80
 length:80
tʰwən↑p⁼u↓ xə↑ iɛ↓ɥ↓↑ s`ɹ`↓ s`ɹ`↑fən→ ʃjɛn↓↑jɛn↓↑ t⁼ə p⁼aɪ↑sə↓.
 length:63
 length:63
ts`⁼ə↓ts`⁼ʊŋ↓↑ niɑʊ↓↑ tʃʰi→ʃi→ ɥ↑ tsʰɹ↓s`əŋ→lin↑, sən→lin↑ xə↑ xwa→ɥæn↑ ts`⁼ʊŋ→[ i→].
 length:85
 length:83
tʰa→

**Tech for good.** For people who will deploy OpenVoice for public usage: We offer you the option to add watermark to avoid potential misuse. Please see the ToneColorConverter class. **MyShell reserves the ability to detect whether an audio is generated by OpenVoice**, no matter whether the watermark is added or not.